<a href="https://colab.research.google.com/github/nu-collab-notebook/CityData/blob/SetUp/CityData.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

#Section 1 **Set Up Environment**

Please Select which city data you wish to load from the drop down provided after running this cell.

In [2]:
# Cell 1 Handles setting up the notebook with the correct datasets to work on
import sys
from google.colab import drive

# Mount Google Drive and setup paths
drive.mount('/content/drive/')
sys.path.append("/content/drive/MyDrive/CityDataNotebook/")

#import background scripts and other imports
from pythonScripts import start_up_manager
from pythonScripts.start_up_manager import *

# Display UI for city selection
display(start_up_manager.build_ui())

# Function to update the config when a new city is selected
def on_city_change(change):
    global config  # Global value for config
    config = start_up_manager.update_config()

start_up_manager.city_selector.observe(on_city_change, names="value")# Listener for config updates

config = start_up_manager.update_config()# loads config(defaults to Dundee unless specified)


Drive already mounted at /content/drive/; to attempt to forcibly remount, call drive.mount("/content/drive/", force_remount=True).


In [3]:
#Cell 2 displays the map centered on the city with boundaries displayed
display(map_renderer.display_city_map(config))

Map(center=[56.476401691737124, -2.9620267318538933], controls=(ZoomControl(options=['position', 'zoom_in_text…

#Section 2 **Postcode Section**

In [4]:
# Cell 1 here loads the postcode data CSV file
import pandas as pd
df = pd.read_csv(config.pc_dundeePostcodes)

# Display the first few rows so we know what the raw data has
print(df.head())

  Postcode In Use?   Latitude  Longitude   Easting  Northing  Grid Ref  \
0  DD1 1AA      No  56.462189  -2.973622  340102.0  730430.0  NO401304   
1  DD1 1AB      No  56.462096  -2.973977  340080.0  730420.0  NO400304   
2  DD1 1AD     Yes  56.462393  -2.977250  339879.0  730456.0  NO398304   
3  DD1 1AE     Yes  56.462730  -2.977778  339847.0  730494.0  NO398304   
4  DD1 1AF     Yes  56.460223  -2.975555  339980.0  730213.0  NO399302   

   County     District       Ward  ... LSOA21 Code  \
0     NaN  Dundee City  Maryfield  ...         NaN   
1     NaN  Dundee City  Maryfield  ...         NaN   
2     NaN  Dundee City  Maryfield  ...         NaN   
3     NaN  Dundee City  Maryfield  ...         NaN   
4     NaN  Dundee City  Maryfield  ...         NaN   

  Lower layer super output area 2021 MSOA21 Code  \
0                                NaN         NaN   
1                                NaN         NaN   
2                                NaN         NaN   
3                     

In [8]:
# cell 2 cleans the data and displays a bit data to show the cleaned data to get the necessary columns and filters to just dundee city

# Load postcodes
df = data_manager.load_postcodes(config)

# Display cleaned postcodes
if df is not None:
    print(df.head())

    # Load pre-filtered postcodes. For now just the city and city center (TODO make this more dynamic for various focus points)
    df_inside_city, df_inside_centre = data_manager.load_filtered_postcodes(config)

✅ Loaded 11527 valid postcodes for dundee.
  Postcode   Latitude  Longitude
0  DD1 1AA  56.462189  -2.973622
1  DD1 1AB  56.462096  -2.973977
2  DD1 1AD  56.462393  -2.977250
3  DD1 1AE  56.462730  -2.977778
4  DD1 1AF  56.460223  -2.975555
Loading and filtering postcodes...
✅ Loaded 11527 valid postcodes for dundee.
Found 6232 postcodes inside the city boundary.
Found 533 postcodes inside the city centre.


In [7]:
# Cell 3 displays postcodes for the city boundary
# this error check will be moved to the background script
# Could make Cell 3 and 4 of this section into one cell with a dropdown to select..
if config is None or df_inside_city is None:
    print("Error: No city selected or postcode data missing.")
else:
    print("Generating postcode map..... Please wait.")
    m = map_renderer.display_postcodes(df_inside_city, config, boundary_type="city_centre")
    display(m)


Generating postcode map... Please wait.
Generating postcode map with boundary...
Boundary added to the map!


In [9]:
# Cell 4 displays postcodes for the city centre boundary
if config is None or df_inside_city is None:
    print("Error: No city selected or postcode data missing.")
else:
    print("Generating postcode map....... Please wait.")
    m = map_renderer.display_postcodes(df_inside_centre, config, boundary_type="city_centre")
    display(m)

Generating postcode map....... Please wait.
Generating postcode map with boundary...
Boundary added to the map!


# **Routing test example**

**Please Add two markers (allow time between re-positioning)**

In [11]:
# Cell 3 allows for adding markers tothe map which can be used to test routing.
from ipywidgets import Button, VBox
from pythonScripts import marker_manager, map_renderer, data_manager

# Load city config
#config = data_manager.load_city_config(city)

# Render the map with boundary
marker_map = map_renderer.render_map(config, "b_cityBoundry_path")

# Add marker cluster layer
marker_map.add_layer(marker_manager.marker_cluster)

# UI Buttons for adding/removing markers
add_marker_button = Button(description="Add Marker", button_style='info')
add_marker_button.on_click(lambda b: marker_manager.add_marker(marker_map, config))

delete_marker_button = Button(description="Delete Selected", button_style='danger')
delete_marker_button.on_click(lambda b: marker_manager.delete_selected_marker(marker_map))

# Click event to finalize marker placement
marker_map.on_interaction(lambda **kwargs: marker_manager.confirm_marker_placement(marker_map, **kwargs))

# Display marker controls and map
display(marker_map)
display(VBox([add_marker_button, marker_manager.marker_list, delete_marker_button]))
display(marker_manager.marker_output)


Map(center=[56.476401691737124, -2.9620267318538933], controls=(ZoomControl(options=['position', 'zoom_in_text…

Output()

To display a route between the two above markers press the green button bellow. the distance between the two routes is also provided in km

In [12]:
# Cell 4 Generates routes from the two marker points created in the previous cell.
# Currently  the API used (OSRM) seem to just provide driving routes dispite selecting other modes.

from ipywidgets import Dropdown, Button, VBox
from pythonScripts import route_analyser, marker_manager

global_latest_route = None
global_latest_transport_mode = "driving"

transport_selector = Dropdown(
    options={"Driving": "driving", "Walking": "foot", "Cycling": "bike"},
    value="driving",
    description="Transport:",
)

route_output  = route_analyser.route_output

def create_route():
    """ Generates and stores a route using the selected transport mode. """
    global global_latest_route, global_latest_transport_mode
    global_latest_transport_mode = transport_selector.value
    global_latest_route = route_analyser.generate_route(config, global_latest_transport_mode, marker_manager.marker_locations)

    if global_latest_route:
        print("Route successfully stored in global_latest_route.")
    else:
        print("Route generation failed.")

# Button to generate route
route_button = Button(description="Create Route", button_style='success')
route_button.on_click(lambda b: create_route())

display(VBox([transport_selector, route_button, route_output]))


Select from the list to display available location boundaries. You can also check if the above route intersects with any of them.

In [7]:
#cell 5 displays selected boundaries aswell as routes that intersect with any of the boundaries.
from ipywidgets import Dropdown, Button, VBox
from pythonScripts import map_renderer, intersection_checker, route_analyser, marker_manager

#config = data_manager.load_city_config(city)

boundary_output = Output()

boundary_options = {"No Boundaries Available": None} # default empty




    # Boundary selection dropdown
boundary_selector = Dropdown(
        options = boundary_options,
        value = None,  # will set a default if one exists
        description="Boundary:",
    )

if config is None:
    print("Error: No valid city config found. Please re-select a city in the first cell.")
else:
    # Get all available boundaries dynamically
    boundary_options = {key: key for key in dir(config) if key.startswith("b_")}

    # checks at least one valid boundary, otherwise set options to an empty dictionary
    if not boundary_options:
        print(f"⚠ Warning: No boundaries found in config for {config.CITY_NAME}.")
        boundary_options = {"No Boundaries Available": None}

    # Use first available boundary if it exists
    default_boundary = next(iter(boundary_options.keys()), None)

    # Update boundary selector with valid options
    boundary_selector.options = boundary_options
    boundary_selector.value = default_boundary  # Will set default only if one exists


def update_boundary_map():
    """ Updates the displayed boundary map. """
    with boundary_output:
        boundary_output.clear_output()
       # config = data_manager.load_city_config(config)
        if config:
            display(map_renderer.render_map(config, boundary_selector.value))
        else:
            print("Error: No valid city was selected. Please re-select a city in the first cell to properly load the config file.")

def check_route_intersection():
    """ Checks if the current route intersects with the selected boundary. """
    with boundary_output:

        boundary_output.clear_output()

        if global_latest_route is None:
            print("No valid route found. Please generate a route first.")
            return

        print("Checking for intersections...")
        intersection_checker.check_intersection(config, boundary_selector.value, global_latest_route)

# Buttons to update the boundary and check intersections
boundary_button = Button(description="Show Boundary", button_style='primary')
boundary_button.on_click(lambda b: update_boundary_map())

intersection_button = Button(description="Check Against Route", button_style='warning')
intersection_button.on_click(lambda b: check_route_intersection())

display(VBox([boundary_selector, boundary_button, intersection_button, boundary_output]))
